In [1]:
%run inference__1_loading.ipynb

In [2]:
import numpy as np
import pandas_bokeh
pandas_bokeh.output_notebook()
pd.set_option('plotting.backend', 'pandas_bokeh')

Loading BokehJS ...

In [3]:
input_files[:5]

[PosixPath('/home/paulo/Documents/mba_tcc/data/2_final/0__input/001_UCR_Anomaly_DISTORTED1sddb40_35000_52000_52620.parquet'),
 PosixPath('/home/paulo/Documents/mba_tcc/data/2_final/0__input/002_UCR_Anomaly_DISTORTED2sddb40_35000_56600_56900.parquet'),
 PosixPath('/home/paulo/Documents/mba_tcc/data/2_final/0__input/003_UCR_Anomaly_DISTORTED3sddb40_35000_46600_46900.parquet'),
 PosixPath('/home/paulo/Documents/mba_tcc/data/2_final/0__input/004_UCR_Anomaly_DISTORTEDBIDMC1_2500_5400_5600.parquet'),
 PosixPath('/home/paulo/Documents/mba_tcc/data/2_final/0__input/005_UCR_Anomaly_DISTORTEDCIMIS44AirTemperature1_4000_5391_5392.parquet')]

In [4]:
file_index = pd.read_parquet(file_index_path / "files_index.parquet")

In [5]:
train_file = pd.read_parquet(input_files[0])

In [6]:
file_infos = file_index[file_index.file_number == 1].filter(regex="(file|anomaly)").to_dict(orient="records")[0]
file_infos

{'file_path': '/home/paulo/Documents/mba_tcc/data/0_raw/UCR_Anomaly_FullData/001_UCR_Anomaly_DISTORTED1sddb40_35000_52000_52620.txt',
 'file_name': '001_UCR_Anomaly_DISTORTED1sddb40_35000_52000_52620.txt',
 'file_number': 1,
 'anomaly_index_start': 52000,
 'anomaly_index_end': 52620}

In [7]:
# train_file.vals.plot.line()

In [8]:
# train_file[train_file.anomaly_set == 1].plot.line()

In [9]:
from sklearn.preprocessing import FunctionTransformer

from pandas.core.window.rolling import Rolling

In [21]:
def sigma_series(df, col_name, w=3, sigma=3):
    df_rolling: Rolling = df[col_name].rolling(window=w, center=True)
    
    df_rolling_mean = df_rolling.mean()
    df_rolling_std = df_rolling.std()

    new_cols = {
        (col_name, "mean", str(w), "w"): df_rolling_mean,
        (col_name, "std", str(w), "w"): df_rolling_std,
        (col_name, "lower", str(w), "w", str(sigma), "s"): df_rolling_mean - sigma * df_rolling_std,
        (col_name, "upper", str(w), "w", str(sigma), "s"): df_rolling_mean + sigma * df_rolling_std,
    }
    return df.assign(**{"_".join(k): v for k, v in new_cols.items()}).drop(columns=["train_set", "test_set", "anomaly_set", "vals"])


In [22]:
from functools import reduce

In [23]:
result_list = [train_file[train_file.anomaly_set == 1]] + [
    # sigma_series(test_tagged[test_tagged.is_anomaly == 1], "vals", w=30),
    # sigma_series(train_file[train_file.anomaly_set == 1], "vals", w=30).drop(columns=["vals", "anomaly_set"]),
    # sigma_series(test_tagged[test_tagged.is_anomaly == 1], "vals", w=50).drop(columns=["vals", "is_anomaly"]),
    sigma_series(train_file[train_file.anomaly_set == 1], "vals", w=i)
    for i in range(2, 31)
]

# result = reduce(lambda x, y: x.merge(y, how="left", left_index=True, right_index=True), result_list)
result = pd.concat(result_list, axis=1)

In [ ]:
result.info(verbose=True)

In [32]:
# for i in range(6):
i = 0
b = 20

result.filter(regex="std").plot.line(figsize=(1200, 600))

Figure(id='17899', ...)

In [14]:
#result.head()

In [15]:
#result.describe(percentiles=np.arange(0., 1., .05))

In [16]:
#result.to_dict(orient="records")